<p style='margin: 12px; font-size: 36px; text-align:center'>Driving LLDB from Python</p>

Locating the python lldb module:

* On mac, when brewed, `lldb -P` works
* On Ubuntu-20.4, it's wrong with lldb-12 at least. You can try to locate the "embedded_interpreter.py" instead

In [1]:
!lldb-15 -P

/usr/lib/lib/python3.8/site-packages


In [2]:
!LD_LIBRARY_PATH='/media/DataExt4/Software/Others/llvm-project/build-release/bin/' /media/DataExt4/Software/Others/llvm-project/build-release/bin/lldb -P

/media/DataExt4/Software/Others/llvm-project/build-release/lib/python3.9/site-packages


In [3]:
# or `find /usr/ -name "embedded_interpreter.py"`
!mlocate "embedded_interpreter.py"

/snap/clion/198/bin/lldb/linux/lib/python3.8/site-packages/lldb/embedded_interpreter.py
/snap/clion/203/bin/lldb/linux/lib/python3.8/site-packages/lldb/embedded_interpreter.py


In [4]:
import os
from pathlib import Path
import platform
import sys

if platform.system() == 'Linux':
    #lldb_path = '/usr/lib/llvm-12/lib/python3/dist-packages'
    # sys.path.insert(0, '/usr/lib/llvm-15/lib/python3.8/site-packages')
    # sys.path.insert(1, '/usr/lib/llvm-15/lib/python3/dist-packages')
    sys.path.insert(0, '/media/DataExt4/Software/Others/llvm-project/build-release/lib/python3.9/site-packages')
elif platform.system() == 'Darwin':
    lldb_path = '/opt/homebrew/Cellar/llvm/14.0.6_1/libexec/python3.10/site-packages'
else:
    raise ValueError("Dunno where to find lldb, locate it yourself")

import lldb

https://github.com/llvm/llvm-project/blob/main/lldb/packages/Python/lldbsuite/test/lldbutil.py

In [5]:
from enum import Enum

class LLDBState(Enum):
    Invalid = lldb.eStateInvalid
    Unloaded = lldb.eStateUnloaded
    Connected = lldb.eStateConnected
    Attaching = lldb.eStateAttaching
    Launching = lldb.eStateLaunching
    Stopped = lldb.eStateStopped
    Running = lldb.eStateRunning
    Stepping = lldb.eStateStepping
    Crashed = lldb.eStateCrashed
    Detached = lldb.eStateDetached
    Exited = lldb.eStateExited
    Suspended = lldb.eStateSuspended

In [6]:
def display_frame(thread: lldb.SBThread):
    frame = thread.GetSelectedFrame()
    debugger = thread.GetProcess().GetTarget().GetDebugger()
    source_mgr = debugger.GetSourceManager()
    # Use a string stream as the destination.
    stream = lldb.SBStream()
    lineEntry = frame.GetLineEntry()
    line_num = lineEntry.GetLine()
    fileSpec = lineEntry.GetFileSpec()
    source_mgr.DisplaySourceLinesWithLineNumbers(fileSpec,
                                                 line_num,
                                                 10, # context before
                                                 10, # context after
                                                 '=>', # prefix for current line
                                                 stream)
    print(stream.GetData())

In [7]:
def display_breakpoints(target: lldb.SBTarget):
    print(f"There are {target.num_breakpoints} breakpoints\n")
    for b in target.breakpoint_iter():
        print(b)
        for l in b.get_breakpoint_location_list():
            print("  " + str(l))
        print("")

# Basic example

Compile a dumb cpp file into an excutable in the build directory

In [8]:
out_dir = Path('build').resolve()
out_dir.mkdir(exist_ok=True)

In [9]:
!g++ -std=c++20 -O0 -g main.cpp -o build/test && ./build/test

1 0 


In [10]:
exe = str(Path('build/test').resolve())

In [11]:
# Create a new debugger instance
debugger = lldb.SBDebugger.Create()

# We want pretty colors!
debugger.SetUseColor(True)

# When we step or continue, don't return from the function until the process
# stops. We do this by setting the async mode to false.
debugger.SetAsync(False)

# Create a target from a file and arch
print(f"Creating a target for '{exe}'")

target = debugger.CreateTargetWithFileAndArch (exe, lldb.LLDB_ARCH_DEFAULT)

if not target:
    raise ValueError(f"Failed to create a target for '{exe}'")
    
# If the target is valid set a breakpoint at main
fname = 'main'
main_bp = target.BreakpointCreateByName (fname, target.GetExecutable().GetFilename())
print(main_bp)

Creating a target for '/home/julien/Software/LLDBScripting/build/test'
SBBreakpoint: id = 1, name = 'main', module = test, locations = 1


### Normal launch

In [12]:
# Launch the process. Since we specified synchronous mode, we won't return
# from this function until we hit the breakpoint at main
process = target.LaunchSimple(argv=None, envp=None, working_directory=os.getcwd())

# Make sure the launch went ok
assert process

### Debug Launch

In [13]:
target.IsValid()

True

In [14]:
thread = process.GetSelectedThread()
assert thread

print(f"There are {thread.GetNumFrames()} Frames")
for frame in thread.get_thread_frames():
    print(frame)

There are 3 Frames
frame #0: 0x0000555555559f0c test`main at main.cpp:6:78
frame #1: 0x00007ffff7b92083 libc.so.6`__libc_start_main(main=(test`main at main.cpp:5:12), argc=1, argv=0x00007fffffffc738, init=<unavailable>, fini=<unavailable>, rtld_fini=<unavailable>, stack_end=0x00007fffffffc728) at libc-start.c:308:16
frame #2: 0x0000555555559e2e test`_start + 46


In [15]:
# Get the current frame
frame = thread.GetSelectedFrame()
assert(frame)
print(frame)

frame #0: 0x0000555555559f0c test`main at main.cpp:6:78


In [16]:
source_mgr = debugger.GetSourceManager()
# Use a string stream as the destination.
stream = lldb.SBStream()
lineEntry = frame.GetLineEntry()
line_num = lineEntry.GetLine()
fileSpec = lineEntry.GetFileSpec()
source_mgr.DisplaySourceLinesWithLineNumbers(fileSpec,
                                             line_num,
                                             10, # context before
                                             10, # context after
                                             '=>', # prefix for current line
                                             stream)
print(stream.GetData())

   1   	#include <iostream>
   2   	#include <string>
   3   	#include <vector>
   4   	
   5   	int main() {
=> 6   	  std::vector<std::string> vec{"First string", "Second String that is longer"};
   7   	  std::vector<int> intVec;
   8   	  intVec.resize(vec.size(), -1);
   9   	  std::vector<bool> moved;
   10  	  moved.resize(vec.size(), false);
   11  	
   12  	  int newPos = 0;
   13  	  for (int i = 0; auto& s : vec) {
   14  	    if (s.size() > 20) {
   15  	      moved[i] = true;
   16  	      intVec[newPos++] = i;
   17  	    }
   18  	    ++i;
   19  	  }
   20  	
   21  	  for (int i = 0; auto& s : vec) {



In [17]:
thread.StepOver()
assert LLDBState(process.GetState()) == LLDBState.Stopped
display_frame(thread)

   1   	#include <iostream>
   2   	#include <string>
   3   	#include <vector>
   4   	
   5   	int main() {
   6   	  std::vector<std::string> vec{"First string", "Second String that is longer"};
=> 7   	  std::vector<int> intVec;
   8   	  intVec.resize(vec.size(), -1);
   9   	  std::vector<bool> moved;
   10  	  moved.resize(vec.size(), false);
   11  	
   12  	  int newPos = 0;
   13  	  for (int i = 0; auto& s : vec) {
   14  	    if (s.size() > 20) {
   15  	      moved[i] = true;
   16  	      intVec[newPos++] = i;
   17  	    }
   18  	    ++i;
   19  	  }
   20  	
   21  	  for (int i = 0; auto& s : vec) {



In [18]:
thread.StepOver()
assert LLDBState(process.GetState()) == LLDBState.Stopped
display_frame(thread)

   1   	#include <iostream>
   2   	#include <string>
   3   	#include <vector>
   4   	
   5   	int main() {
   6   	  std::vector<std::string> vec{"First string", "Second String that is longer"};
   7   	  std::vector<int> intVec;
=> 8   	  intVec.resize(vec.size(), -1);
   9   	  std::vector<bool> moved;
   10  	  moved.resize(vec.size(), false);
   11  	
   12  	  int newPos = 0;
   13  	  for (int i = 0; auto& s : vec) {
   14  	    if (s.size() > 20) {
   15  	      moved[i] = true;
   16  	      intVec[newPos++] = i;
   17  	    }
   18  	    ++i;
   19  	  }
   20  	
   21  	  for (int i = 0; auto& s : vec) {



In [19]:
process.Continue()
assert LLDBState(process.GetState()) == LLDBState.Exited

# More complex example

## Create a debugger and a target

In [20]:
exe_path = Path('~').expanduser() / 'Software/Others/EnergyPlus-build/Products/energyplus'

In [21]:
# Create a new debugger instance
debugger = lldb.SBDebugger.Create()

# We want pretty colors!
debugger.SetUseColor(True)

# When we step or continue, don't return from the function until the process
# stops. We do this by setting the async mode to false.
debugger.SetAsync(False)

# Create a target from a file and arch
print(f"Creating a target for '{exe_path}'")

target = debugger.CreateTargetWithFileAndArch (str(exe_path), lldb.LLDB_ARCH_DEFAULT)

if not target:
    raise ValueError(f"Failed to create a target for '{exe_path}'")

Creating a target for '/home/julien/Software/Others/EnergyPlus-build/Products/energyplus'


In [22]:
target.GetExecutable().GetFilename()

'energyplus'

## Breakpoints

In [23]:
fname = 'CreateMissingSpaces'
bp1 = target.BreakpointCreateByName (fname) # , target.GetExecutable().GetFilename())
print(bp1)

SBBreakpoint: id = 1, name = 'CreateMissingSpaces', locations = 0


In [24]:
bp2 = target.BreakpointCreateByLocation('SurfaceGeometry.cc', 1566)
print(bp2)

SBBreakpoint: id = 2, file = 'SurfaceGeometry.cc', line = 1566, exact_match = 0, locations = 0


In [25]:
display_breakpoints(target=target)

There are 2 breakpoints

SBBreakpoint: id = 1, name = 'CreateMissingSpaces', locations = 0

SBBreakpoint: id = 2, file = 'SurfaceGeometry.cc', line = 1566, exact_match = 0, locations = 0



## Start process with args

In [26]:
debugger.HandleCommand("settings set target.process.thread.step-out-avoid-nodebug true")
debugger.HandleCommand("type synthetic add --regex '^std::__debug::vector<.+>(( )?&)?$' --python-class lldb.formatters.cpp.gnu_libstdcpp.StdVectorSynthProvider -C true")

In [27]:
EP_DIR = exe_path.parent.parent.parent / 'EnergyPlus/'
assert EP_DIR.exists()
epw = EP_DIR / 'weather/USA_IL_Chicago-OHare.Intl.AP.725300_TMY3.epw'
idf = EP_DIR / 'testfiles/DaylightingDeviceTubular.idf'
assert epw.exists()
assert idf.exists()

In [28]:
argv = ["-D", "-r", "-w", str(epw), "-d", "out-temp", str(idf)] 
print(" ".join(argv))

-D -r -w /home/julien/Software/Others/EnergyPlus/weather/USA_IL_Chicago-OHare.Intl.AP.725300_TMY3.epw -d out-temp /home/julien/Software/Others/EnergyPlus/testfiles/DaylightingDeviceTubular.idf


In [29]:
# Launch the process. Since we specified synchronous mode, we won't return
# from this function until we hit the breakpoint at main
process = target.LaunchSimple(argv=argv, envp=None, working_directory=os.getcwd())

# Make sure the launch went ok
assert process

In [30]:
print(process.GetSTDOUT(1000000))

EnergyPlus Starting
EnergyPlus, Version 22.2.0-78df3bdccc, YMD=2022.08.03 14:22
Adjusting Air System Sizing
Adjusting Standard 62.1 Ventilation Sizing
Initializing Simulation



In [31]:
# Make sure the launch went ok
if process:
    # Print some simple process info
    state = process.GetState()
    print(process)

SBProcess: pid = 376594, state = stopped, threads = 1, executable = energyplus


In [32]:
assert state == lldb.eStateStopped
assert LLDBState(state) == LLDBState.Stopped

In [33]:
bp1.GetNumLocations(), bp1.GetNumResolvedLocations(), bp1.IsEnabled()

(1, 1, True)

In [34]:
bp2.GetNumLocations(), bp2.GetNumResolvedLocations(), bp2.IsEnabled()

(1, 1, True)

In [35]:
for bl in bp2:
    print('breakpoint location load addr: %s' % hex(bl.GetLoadAddress()))
    if bl.GetCondition():
        print('breakpoint location condition: %s' % hex(bl.GetCondition()))

breakpoint location load addr: 0x7ffff064df21


In [36]:
# Get the first thread
# thread = process.GetThreadAtIndex(0)
# Get the current thread
thread = process.GetSelectedThread()
assert thread

In [37]:
print(thread)

thread #1: tid = 376594, 0x00007ffff064df21 libenergyplusapi.so.22.2.0`EnergyPlus::SurfaceGeometry::GetSurfaceData(state=0x00007fffffffb040, ErrorsFound=0x00007fffffffab41) at SurfaceGeometry.cc:1566:65, name = 'energyplus', stop reason = breakpoint 2.1


In [38]:
thread.GetNumFrames()

12

In [39]:
for frame in thread.get_thread_frames():
    print(frame)

frame #0: 0x00007ffff064df21 libenergyplusapi.so.22.2.0`EnergyPlus::SurfaceGeometry::GetSurfaceData(state=0x00007fffffffb040, ErrorsFound=0x00007fffffffab41) at SurfaceGeometry.cc:1566:65
frame #1: 0x00007ffff063c11a libenergyplusapi.so.22.2.0`EnergyPlus::SurfaceGeometry::SetupZoneGeometry(state=0x00007fffffffb040, ErrorsFound=0x00007fffffffab41) at SurfaceGeometry.cc:351:23
frame #2: 0x00007fffeea4e56c libenergyplusapi.so.22.2.0`EnergyPlus::HeatBalanceManager::GetBuildingData(state=0x00007fffffffb040, ErrorsFound=0x00007fffffffab41) at HeatBalanceManager.cc:4910:43
frame #3: 0x00007fffee9e414a libenergyplusapi.so.22.2.0`EnergyPlus::HeatBalanceManager::GetHeatBalanceInput(state=0x00007fffffffb040) at HeatBalanceManager.cc:328:24
frame #4: 0x00007fffee9e36c2 libenergyplusapi.so.22.2.0`EnergyPlus::HeatBalanceManager::ManageHeatBalance(state=0x00007fffffffb040) at HeatBalanceManager.cc:204:32
frame #5: 0x00007ffff0256ba8 libenergyplusapi.so.22.2.0`EnergyPlus::SimulationManager::SetupSimul

In [40]:
# Get the first frame
# frame = thread.GetFrameAtIndex(0)
# Get the current frame
frame = thread.GetSelectedFrame()
assert(frame)
print(frame)

frame #0: 0x00007ffff064df21 libenergyplusapi.so.22.2.0`EnergyPlus::SurfaceGeometry::GetSurfaceData(state=0x00007fffffffb040, ErrorsFound=0x00007fffffffab41) at SurfaceGeometry.cc:1566:65


In [41]:
source_mgr = debugger.GetSourceManager()
# Use a string stream as the destination.
stream = lldb.SBStream()
lineEntry = frame.GetLineEntry()
line_num = lineEntry.GetLine()
fileSpec = lineEntry.GetFileSpec()
source_mgr.DisplaySourceLinesWithLineNumbers(fileSpec,
                                             line_num,
                                             10, # context before
                                             10, # context after
                                             '=>', # prefix for current line
                                             stream)
print(stream.GetData())

   1556	        //    After reordering, MovedSurfs should equal TotSurfaces
   1557	
   1558	        MovedSurfs = 0;
   1559	        Array1D<bool> SurfaceTmpClassMoved; // Tmp class is moved
   1560	        SurfaceTmpClassMoved.dimension(state.dataSurface->TotSurfaces, false);
   1561	
   1562	        // Old SurfNum to New SurfNum
   1563	        // Old = order in state.dataSurfaceGeometry->SurfaceTmp
   1564	        // New = order in state.dataSurface->Surface
   1565	        EPVector<int> oldToNewSurfNums;
=> 1566	        oldToNewSurfNums.resize(state.dataSurface->TotSurfaces, -1);
   1567	
   1568	        // Move all shading Surfaces to Front
   1569	        for (int SurfNum = 1; SurfNum <= state.dataSurface->TotSurfaces; ++SurfNum) {
   1570	            if (state.dataSurfaceGeometry->SurfaceTmp(SurfNum).Class != SurfaceClass::Detached_F &&
   1571	                state.dataSurfaceGeometry->SurfaceTmp(SurfNum).Class != SurfaceClass::Detached_B &&
   1572	                state.dataSu

## Retrieve array data into a nice python dict

In [42]:
root = frame.FindVariable("state")
assert(root.error.success)
surfaces = root.GetChildMemberWithName('dataSurfaceGeometry').Dereference().GetChildMemberWithName('SurfaceTmp')
assert(surfaces.error.success)
n_surfaces = surfaces.GetChildMemberWithName('size_').GetValueAsUnsigned()


surfaces_ptr = surfaces.GetChildMemberWithName('data_')
surfaceDataType = surfaces_ptr.GetType().GetPointeeType()
surfaceByteSize = surfaceDataType.GetByteSize()   # 1068


construct = root.GetChildMemberWithName('dataConstruction').Dereference().GetChildMemberWithName('Construct')
assert(construct.error.success)
construct_ptr = construct.GetChildMemberWithName('data_')
constructDataType = construct_ptr.GetType().GetPointeeType()
constructByteSize = constructDataType.GetByteSize()   # 7064


def get_and_format_as_string(val, childName):
    return str(val.GetChildMemberWithName(childName)).split(f"{childName} = ")[1].replace('"', '').strip()

infos = []
for i in range (0, n_surfaces):
    offset = surfaces_ptr.GetValueAsUnsigned() + i * surfaceByteSize
    val = target.CreateValueFromAddress("temp", lldb.SBAddress(offset, target), surfaceDataType)
    name =  get_and_format_as_string(val, 'Name')
    zone = val.GetChildMemberWithName('Zone').GetValueAsSigned()
    className = get_and_format_as_string(val, 'Class')
    classInt = val.GetChildMemberWithName('Class').GetValueAsSigned()
    baseSurf = val.GetChildMemberWithName('BaseSurf').GetValueAsSigned()
    baseSurfName = get_and_format_as_string(val, 'BaseSurfName')
    extBoundCond = val.GetChildMemberWithName('ExtBoundCond').GetValueAsSigned()
    extBoundCondName = get_and_format_as_string(val, 'ExtBoundCondName')
    heatTransSurf = val.GetChildMemberWithName('HeatTransSurf').GetValueAsSigned() == 1
    
    construction = val.GetChildMemberWithName('Construction').GetValueAsSigned()
    c_offset = construct_ptr.GetValueAsUnsigned() + (construction - 1) * constructByteSize
    c_val = target.CreateValueFromAddress("temp", lldb.SBAddress(c_offset, target), constructDataType)
    c_name = get_and_format_as_string(c_val, 'Name')
    typeBound = c_val.GetChildMemberWithName('TypeIsAirBoundary').GetValueAsSigned() == 1
    
    print(f"1-index={i+1}, {name=}, {zone=}, {className=}, {baseSurf=}, {baseSurfName=}, {extBoundCond=}, {extBoundCondName=}")
    infos.append({'SurfNum': i + 1, 'Name': name, 'Zone': zone, 'ClassInt': classInt, 'BaseSurf': baseSurf, 'BaseSurfName': baseSurfName,
                  'ExtBoundCond': extBoundCond, 'ExtBoundCondName': extBoundCondName, 'HeatTransSurf': heatTransSurf,
                  'Construction': construction, 'ConstructionName': c_name, 'TypeIsAirBoundary': typeBound})

1-index=1, name='DAYLIT SOUTH WALL', zone=1, className='Wall', baseSurf=1, baseSurfName='DAYLIT SOUTH WALL', extBoundCond=0, extBoundCondName=''
1-index=2, name='DAYLIT WEST WALL', zone=1, className='Wall', baseSurf=2, baseSurfName='DAYLIT WEST WALL', extBoundCond=0, extBoundCondName=''
1-index=3, name='DAYLIT NORTH WALL', zone=1, className='Wall', baseSurf=3, baseSurfName='DAYLIT NORTH WALL', extBoundCond=0, extBoundCondName=''
1-index=4, name='DAYLIT EAST WALL', zone=1, className='Wall', baseSurf=4, baseSurfName='DAYLIT EAST WALL', extBoundCond=0, extBoundCondName=''
1-index=5, name='DAYLIT FLOOR', zone=1, className='Floor', baseSurf=5, baseSurfName='DAYLIT FLOOR', extBoundCond=-999, extBoundCondName='DAYLIT FLOOR'
1-index=6, name='DAYLIT CEILING', zone=1, className='Roof', baseSurf=6, baseSurfName='DAYLIT CEILING', extBoundCond=-999, extBoundCondName='DAYLIT ATTIC FLOOR'
1-index=7, name='DAYLIT ATTIC SOUTH WALL', zone=2, className='Wall', baseSurf=7, baseSurfName='DAYLIT ATTIC SOUTH

In [43]:
infos[:2]

[{'SurfNum': 1,
  'Name': 'DAYLIT SOUTH WALL',
  'Zone': 1,
  'ClassInt': 1,
  'BaseSurf': 1,
  'BaseSurfName': 'DAYLIT SOUTH WALL',
  'ExtBoundCond': 0,
  'ExtBoundCondName': '',
  'HeatTransSurf': True,
  'Construction': 1,
  'ConstructionName': 'EXTWALL80',
  'TypeIsAirBoundary': False},
 {'SurfNum': 2,
  'Name': 'DAYLIT WEST WALL',
  'Zone': 1,
  'ClassInt': 1,
  'BaseSurf': 2,
  'BaseSurfName': 'DAYLIT WEST WALL',
  'ExtBoundCond': 0,
  'ExtBoundCondName': '',
  'HeatTransSurf': True,
  'Construction': 1,
  'ConstructionName': 'EXTWALL80',
  'TypeIsAirBoundary': False}]

## Step over

In [44]:
thread.StepOver()

display_frame(thread)

   1559	        Array1D<bool> SurfaceTmpClassMoved; // Tmp class is moved
   1560	        SurfaceTmpClassMoved.dimension(state.dataSurface->TotSurfaces, false);
   1561	
   1562	        // Old SurfNum to New SurfNum
   1563	        // Old = order in state.dataSurfaceGeometry->SurfaceTmp
   1564	        // New = order in state.dataSurface->Surface
   1565	        EPVector<int> oldToNewSurfNums;
   1566	        oldToNewSurfNums.resize(state.dataSurface->TotSurfaces, -1);
   1567	
   1568	        // Move all shading Surfaces to Front
=> 1569	        for (int SurfNum = 1; SurfNum <= state.dataSurface->TotSurfaces; ++SurfNum) {
   1570	            if (state.dataSurfaceGeometry->SurfaceTmp(SurfNum).Class != SurfaceClass::Detached_F &&
   1571	                state.dataSurfaceGeometry->SurfaceTmp(SurfNum).Class != SurfaceClass::Detached_B &&
   1572	                state.dataSurfaceGeometry->SurfaceTmp(SurfNum).Class != SurfaceClass::Shading)
   1573	                continue;
   1574	
   1575

In [45]:
thread.JumpToLine(fileSpec, 1615)
display_frame(thread)

   1605	                    state.dataSurface->AllSurfaceListReportOrder.push_back(SurfNum);
   1606	                }
   1607	                oldToNewSurfNums(SurfNum) = MovedSurfs;
   1608	                SurfaceTmpClassMoved(SurfNum) = true; //'Moved'
   1609	            }
   1610	
   1611	            //  For each Base Surface Type (Wall, Floor, Roof/Ceiling) - put these first
   1612	
   1613	            for (int Loop = 1; Loop <= 3; ++Loop) {
   1614	
=> 1615	                for (int SurfNum = 1; SurfNum <= state.dataSurface->TotSurfaces; ++SurfNum) {
   1616	
   1617	                    if (SurfaceTmpClassMoved(SurfNum)) continue;
   1618	                    if (state.dataSurfaceGeometry->SurfaceTmp(SurfNum).Zone == 0) continue;
   1619	
   1620	                    if (!UtilityRoutines::SameString(state.dataSurfaceGeometry->SurfaceTmp(SurfNum).ZoneName, state.dataHeatBal->Zone(ZoneNum).Name))
   1621	                        continue;
   1622	                    if (state.dataSurf

In [46]:
thread.JumpToLine(fileSpec, 1772)
display_frame(thread)

   1762	                                    std::string{RoutineName} + "Error in Surface= \"" + state.dataSurfaceGeometry->SurfaceTmp(Loop).Name +
   1763	                                        " indicated Zone=\"" + state.dataSurfaceGeometry->SurfaceTmp(Loop).ZoneName + "\"");
   1764	                }
   1765	            }
   1766	            ShowWarningError(state,
   1767	                             std::string{RoutineName} +
   1768	                                 "Remaining surface checks will use \"reordered number of surfaces\", not number of original surfaces");
   1769	        }
   1770	
   1771	        // Realign the relationship: surface to base surface
=> 1772	        for (int SurfNum = 1; SurfNum <= state.dataSurface->TotSurfaces; ++SurfNum) {
   1773	            auto &movedSurf = state.dataSurface->Surface(SurfNum);
   1774	            if (movedSurf.BaseSurf > 0) {
   1775	                int newBaseSurfNum = oldToNewSurfNums(movedSurf.BaseSurf);
   1776	             

In [47]:
oldToNewSurfNums = frame.FindVariable("oldToNewSurfNums")
assert(oldToNewSurfNums.error.success)
assert(oldToNewSurfNums.GetTypeName() == 'EnergyPlus::EPVector<int>')
vec = oldToNewSurfNums.GetChildAtIndex(0)

In [48]:
print(oldToNewSurfNums)

(EnergyPlus::EPVector<int>) oldToNewSurfNums = {
  std::__debug::vector<int, std::allocator<> > = size=28 {
    __gnu_debug::_Safe_container<std::__debug::vector<int, std::allocator<> >, std::allocator<>, __gnu_debug::_Safe_sequence, true> = {
      __gnu_debug::_Safe_sequence<std::__debug::vector<int, std::allocator<> > > = {
        __gnu_debug::_Safe_sequence_base = {
          _M_iterators = nullptr
          _M_const_iterators = nullptr
          _M_version = 2
        }
      }
    }
    std::__cxx1998::vector<int, std::allocator<> > = size=0 {
      std::__cxx1998::_Vector_base<int, std::allocator<> > = {
        _M_impl = {
          std::__cxx1998::_Vector_base<int, std::allocator<> >::_Vector_impl_data = {
            _M_start = 0x0000555555c66060
            _M_finish = 0x0000555555c660d0
            _M_end_of_storage = 0x0000555555c660d0
          }
        }
      }
    }
    __gnu_debug::_Safe_vector<std::__debug::vector<int, std::allocator<> >, std::__cxx1998::vector<int

In [67]:
res = lldb.SBCommandReturnObject()
ci = debugger.GetCommandInterpreter()
assert(ci)
ci.HandleCommand("type synthetic info oldToNewSurfNums", res)
assert res.Succeeded()
print(res)

Error:  Success
Output Message:
no synthetic applies to (EnergyPlus::EPVector<int>) oldToNewSurfNums


In [68]:
ci.HandleCommand("type synthetic list", res)
assert res.Succeeded()
print(res)

Error:  Success
Output Message:
-----------------------
Category: default
-----------------------
^std::__debug::vector<.+>(( )?&)?$:  Python class lldb.formatters.cpp.gnu_libstdcpp.StdVectorSynthProvider
-----------------------
Category: VectorTypes
-----------------------
-----------------------
Category: system
-----------------------
-----------------------
Category: cplusplus
-----------------------
^std::vector<.+>(( )?&)?$:  Python class lldb.formatters.cpp.gnu_libstdcpp.StdVectorSynthProvider
^std::map<.+> >(( )?&)?$:  Python class lldb.formatters.cpp.gnu_libstdcpp.StdMapLikeSynthProvider
^std::deque<.+>(( )?&)?$:  Python class lldb.formatters.cpp.gnu_libstdcpp.StdDequeSynthProvider
^std::set<.+> >(( )?&)?$:  Python class lldb.formatters.cpp.gnu_libstdcpp.StdMapLikeSynthProvider
^std::multimap<.+> >(( )?&)?$:  Python class lldb.formatters.cpp.gnu_libstdcpp.StdMapLikeSynthProvider
^std::multiset<.+> >(( )?&)?$:  Python class lldb.formatters.cpp.gnu_libstdcpp.StdMapLikeSynthProvi

In [69]:
# This tend to work when compiled with clang on macOS, not on Ubuntu though...
for i in vec.children:
    print(i.GetValueAsSigned())

-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1
-1


In [70]:
n_elements = oldToNewSurfNums.EvaluateExpression('size()').GetValueAsUnsigned()
elements = []
for i in range(1, n_elements + 1):
    elements.append(oldToNewSurfNums.EvaluateExpression(f'({i})').GetValueAsSigned())
elements

[1,
 2,
 3,
 4,
 5,
 6,
 7,
 8,
 9,
 10,
 11,
 12,
 13,
 14,
 15,
 16,
 17,
 18,
 19,
 20,
 21,
 22,
 23,
 24,
 25,
 26,
 27,
 28]

In [71]:
display_frame(thread)

   1762	                                    std::string{RoutineName} + "Error in Surface= \"" + state.dataSurfaceGeometry->SurfaceTmp(Loop).Name +
   1763	                                        " indicated Zone=\"" + state.dataSurfaceGeometry->SurfaceTmp(Loop).ZoneName + "\"");
   1764	                }
   1765	            }
   1766	            ShowWarningError(state,
   1767	                             std::string{RoutineName} +
   1768	                                 "Remaining surface checks will use \"reordered number of surfaces\", not number of original surfaces");
   1769	        }
   1770	
   1771	        // Realign the relationship: surface to base surface
=> 1772	        for (int SurfNum = 1; SurfNum <= state.dataSurface->TotSurfaces; ++SurfNum) {
   1773	            auto &movedSurf = state.dataSurface->Surface(SurfNum);
   1774	            if (movedSurf.BaseSurf > 0) {
   1775	                int newBaseSurfNum = oldToNewSurfNums(movedSurf.BaseSurf);
   1776	             

In [72]:
root = frame.FindVariable("state")
assert(root.error.success)
data_surface = surfaces = root.GetChildMemberWithName('dataSurface').Dereference()
surfaces = data_surface.GetChildMemberWithName('Surface')
assert(surfaces.error.success)
n_surfaces = data_surface.GetChildMemberWithName('TotSurfaces').GetValueAsUnsigned()
n_surfaces

28

In [73]:
allSurfaceListReportOrder = data_surface.GetChildMemberWithName('AllSurfaceListReportOrder')
print(allSurfaceListReportOrder)

(std::vector<int, std::allocator<> >) AllSurfaceListReportOrder = size=0 {}


In [75]:
allSurfaceListReportOrder.GetTypeName()

'std::__debug::vector<int, std::allocator<> >'

In [76]:
print(surfaces.GetChildAtIndex(0).EvaluateExpression('size()'))

 = <could not resolve type>


In [77]:
surfaces.GetTypeName()

'EnergyPlus::EPVector<EnergyPlus::DataSurfaces::SurfaceData>'

## Disassemble / print registers

In [78]:
function = frame.GetFunction()
# See if we have debug info (a function)
assert function
print(function)

SBFunction: id = 0x10738ead, name = EnergyPlus::SurfaceGeometry::GetSurfaceData(EnergyPlus::EnergyPlusData&, bool&), type = GetSurfaceData


In [79]:
print(function.GetInstructions(target))

libenergyplusapi.so.22.2.0[0xa93dcfa]: endbr64 
libenergyplusapi.so.22.2.0[0xa93dcfe]: pushq  %rbp
libenergyplusapi.so.22.2.0[0xa93dcff]: movq   %rsp, %rbp
libenergyplusapi.so.22.2.0[0xa93dd02]: pushq  %r15
libenergyplusapi.so.22.2.0[0xa93dd04]: pushq  %r14
libenergyplusapi.so.22.2.0[0xa93dd06]: pushq  %r13
libenergyplusapi.so.22.2.0[0xa93dd08]: pushq  %r12
libenergyplusapi.so.22.2.0[0xa93dd0a]: pushq  %rbx
libenergyplusapi.so.22.2.0[0xa93dd0b]: subq   $0xa28, %rsp              ; imm = 0xA28 
libenergyplusapi.so.22.2.0[0xa93dd12]: movq   %rdi, -0xa48(%rbp)
libenergyplusapi.so.22.2.0[0xa93dd19]: movq   %rsi, -0xa50(%rbp)
libenergyplusapi.so.22.2.0[0xa93dd20]: movq   %fs:0x28, %rax
libenergyplusapi.so.22.2.0[0xa93dd29]: movq   %rax, -0x38(%rbp)
libenergyplusapi.so.22.2.0[0xa93dd2d]: xorl   %eax, %eax
libenergyplusapi.so.22.2.0[0xa93dd2f]: lock   
libenergyplusapi.so.22.2.0[0xa93dd30]: addq   $0x1, 0x6f738c8(%rip)
libenergyplusapi.so.22.2.0[0xa93dd38]: movb   $0x0, -0xa35(%rbp)
libenergyp

In [80]:
def disassemble_instructions (insts):
    for i in insts:
        print (i)

if frame:
    # Print some simple frame info
    print(frame)
    function = frame.GetFunction()
    # See if we have debug info (a function)
    if function:
        # We do have a function, print some info for the function
        print(function)
        # Now get all instructions for this function and print them
        insts = function.GetInstructions(target)
        disassemble_instructions (insts)
    else:
        # See if we have a symbol in the symbol table for where we stopped
        symbol = frame.GetSymbol();
        if symbol:
            # We do have a symbol, print some info for the symbol
            print(symbol)
            # Now get all instructions for this symbol and print them
            insts = symbol.GetInstructions(target)
            disassemble_instructions (insts)

    registerList = frame.GetRegisters()
    print('Frame registers (size of register set = %d):' % registerList.GetSize())
    for value in registerList:
        #print value
        print('%s (number of children = %d):' % (value.GetName(), value.GetNumChildren()))
        for child in value:
            print('Name: ', child.GetName(), ' Value: ', child.GetValue())

frame #0: 0x00007ffff0651065 libenergyplusapi.so.22.2.0`EnergyPlus::SurfaceGeometry::GetSurfaceData(state=0x00007fffffffb040, ErrorsFound=0x00007fffffffab41) at SurfaceGeometry.cc:1772:18
SBFunction: id = 0x10738ead, name = EnergyPlus::SurfaceGeometry::GetSurfaceData(EnergyPlus::EnergyPlusData&, bool&), type = GetSurfaceData
libenergyplusapi.so.22.2.0[0xa93dcfa]: endbr64 
libenergyplusapi.so.22.2.0[0xa93dcfe]: pushq  %rbp
libenergyplusapi.so.22.2.0[0xa93dcff]: movq   %rsp, %rbp
libenergyplusapi.so.22.2.0[0xa93dd02]: pushq  %r15
libenergyplusapi.so.22.2.0[0xa93dd04]: pushq  %r14
libenergyplusapi.so.22.2.0[0xa93dd06]: pushq  %r13
libenergyplusapi.so.22.2.0[0xa93dd08]: pushq  %r12
libenergyplusapi.so.22.2.0[0xa93dd0a]: pushq  %rbx
libenergyplusapi.so.22.2.0[0xa93dd0b]: subq   $0xa28, %rsp              ; imm = 0xA28 
libenergyplusapi.so.22.2.0[0xa93dd12]: movq   %rdi, -0xa48(%rbp)
libenergyplusapi.so.22.2.0[0xa93dd19]: movq   %rsi, -0xa50(%rbp)
libenergyplusapi.so.22.2.0[0xa93dd20]: movq  

libenergyplusapi.so.22.2.0[0xa93f276]: addq   $0x1, 0x6f72932(%rip)
libenergyplusapi.so.22.2.0[0xa93f27e]: leaq   -0x1f0(%rbp), %rax
libenergyplusapi.so.22.2.0[0xa93f285]: leaq   -0x459002c(%rip), %rsi
libenergyplusapi.so.22.2.0[0xa93f28c]: movq   %rax, %rdi
libenergyplusapi.so.22.2.0[0xa93f28f]: callq  0xc658b60
libenergyplusapi.so.22.2.0[0xa93f294]: lock   
libenergyplusapi.so.22.2.0[0xa93f295]: addq   $0x1, 0x6f7291b(%rip)
libenergyplusapi.so.22.2.0[0xa93f29d]: leaq   -0x1f0(%rbp), %rdx
libenergyplusapi.so.22.2.0[0xa93f2a4]: movq   -0xa48(%rbp), %rax
libenergyplusapi.so.22.2.0[0xa93f2ab]: movq   %rax, %rsi
libenergyplusapi.so.22.2.0[0xa93f2ae]: movq   %rbx, %rdi
libenergyplusapi.so.22.2.0[0xa93f2b1]: callq  0xc6f4680
libenergyplusapi.so.22.2.0[0xa93f2b6]: lock   
libenergyplusapi.so.22.2.0[0xa93f2b7]: addq   $0x1, 0x6f72901(%rip)
libenergyplusapi.so.22.2.0[0xa93f2bf]: movl   %eax, -0x8f8(%rbp)
libenergyplusapi.so.22.2.0[0xa93f2c5]: movq   -0xa48(%rbp), %rax
libenergyplusapi.so.22.2.

libenergyplusapi.so.22.2.0[0xa93f614]: leal   (%rax,%rax), %edx
libenergyplusapi.so.22.2.0[0xa93f617]: movl   -0x944(%rbp), %eax
libenergyplusapi.so.22.2.0[0xa93f61d]: addl   %eax, %edx
libenergyplusapi.so.22.2.0[0xa93f61f]: movl   -0x934(%rbp), %eax
libenergyplusapi.so.22.2.0[0xa93f625]: addl   %eax, %edx
libenergyplusapi.so.22.2.0[0xa93f627]: movl   -0x930(%rbp), %eax
libenergyplusapi.so.22.2.0[0xa93f62d]: addl   %eax, %eax
libenergyplusapi.so.22.2.0[0xa93f62f]: addl   %eax, %edx
libenergyplusapi.so.22.2.0[0xa93f631]: movl   -0x8dc(%rbp), %eax
libenergyplusapi.so.22.2.0[0xa93f637]: addl   %eax, %edx
libenergyplusapi.so.22.2.0[0xa93f639]: movl   -0x92c(%rbp), %eax
libenergyplusapi.so.22.2.0[0xa93f63f]: addl   %eax, %eax
libenergyplusapi.so.22.2.0[0xa93f641]: addl   %eax, %edx
libenergyplusapi.so.22.2.0[0xa93f643]: movl   -0x928(%rbp), %eax
libenergyplusapi.so.22.2.0[0xa93f649]: addl   %eax, %eax
libenergyplusapi.so.22.2.0[0xa93f64b]: addl   %eax, %edx
libenergyplusapi.so.22.2.0[0xa93f

libenergyplusapi.so.22.2.0[0xa940ab5]: lock   
libenergyplusapi.so.22.2.0[0xa940ab6]: addq   $0x1, 0x6f71702(%rip)
libenergyplusapi.so.22.2.0[0xa940abe]: leaq   0x380(%rax), %rdx
libenergyplusapi.so.22.2.0[0xa940ac5]: movl   -0x9f8(%rbp), %eax
libenergyplusapi.so.22.2.0[0xa940acb]: movl   %eax, %esi
libenergyplusapi.so.22.2.0[0xa940acd]: movq   %rdx, %rdi
libenergyplusapi.so.22.2.0[0xa940ad0]: callq  0xc7d5b90
libenergyplusapi.so.22.2.0[0xa940ad5]: jmp    0xa940aec
libenergyplusapi.so.22.2.0[0xa940ad7]: endbr64 
libenergyplusapi.so.22.2.0[0xa940adb]: movq   %rax, %rbx
libenergyplusapi.so.22.2.0[0xa940ade]: lock   
libenergyplusapi.so.22.2.0[0xa940adf]: addq   $0x1, 0x6f716c9(%rip)
libenergyplusapi.so.22.2.0[0xa940ae7]: jmp    0xa964218
libenergyplusapi.so.22.2.0[0xa940aec]: lock   
libenergyplusapi.so.22.2.0[0xa940aed]: addq   $0x1, 0x6f716db(%rip)
libenergyplusapi.so.22.2.0[0xa940af5]: movsd  0x78(%rax), %xmm0         ; xmm0 = mem[0],zero 
libenergyplusapi.so.22.2.0[0xa940afa]: movsd 

libenergyplusapi.so.22.2.0[0xa940e8c]: movq   %rax, %rdi
libenergyplusapi.so.22.2.0[0xa940e8f]: callq  0xc66bc30
libenergyplusapi.so.22.2.0[0xa940e94]: lock   
libenergyplusapi.so.22.2.0[0xa940e95]: addq   $0x1, 0x6f71423(%rip)
libenergyplusapi.so.22.2.0[0xa940e9d]: leaq   0x380(%rax), %rdx
libenergyplusapi.so.22.2.0[0xa940ea4]: movl   -0x9f8(%rbp), %eax
libenergyplusapi.so.22.2.0[0xa940eaa]: movl   %eax, %esi
libenergyplusapi.so.22.2.0[0xa940eac]: movq   %rdx, %rdi
libenergyplusapi.so.22.2.0[0xa940eaf]: callq  0xc7d5b90
libenergyplusapi.so.22.2.0[0xa940eb4]: jmp    0xa940ecb
libenergyplusapi.so.22.2.0[0xa940eb6]: endbr64 
libenergyplusapi.so.22.2.0[0xa940eba]: movq   %rax, %rbx
libenergyplusapi.so.22.2.0[0xa940ebd]: lock   
libenergyplusapi.so.22.2.0[0xa940ebe]: addq   $0x1, 0x6f713ea(%rip)
libenergyplusapi.so.22.2.0[0xa940ec6]: jmp    0xa964218
libenergyplusapi.so.22.2.0[0xa940ecb]: lock   
libenergyplusapi.so.22.2.0[0xa940ecc]: addq   $0x1, 0x6f713fc(%rip)
libenergyplusapi.so.22.2.0

...

libenergyplusapi.so.22.2.0[0xa95e5f6]: jmp    0xa95e608
libenergyplusapi.so.22.2.0[0xa95e5f8]: endbr64 
libenergyplusapi.so.22.2.0[0xa95e5fc]: movq   %rax, %rbx
libenergyplusapi.so.22.2.0[0xa95e5ff]: lock   
libenergyplusapi.so.22.2.0[0xa95e600]: addq   $0x1, 0x6f54580(%rip)
libenergyplusapi.so.22.2.0[0xa95e608]: leaq   -0x240(%rbp), %rax
libenergyplusapi.so.22.2.0[0xa95e60f]: movq   %rax, %rdi
libenergyplusapi.so.22.2.0[0xa95e612]: callq  0xc658f60
libenergyplusapi.so.22.2.0[0xa95e617]: lock   
libenergyplusapi.so.22.2.0[0xa95e618]: addq   $0x1, 0x6f5c848(%rip)
libenergyplusapi.so.22.2.0[0xa95e620]: leaq   -0x1f0(%rbp), %rax
libenergyplusapi.so.22.2.0[0xa95e627]: movq   %rax, %rdi
libenergyplusapi.so.22.2.0[0xa95e62a]: callq  0xc658f60
libenergyplusapi.so.22.2.0[0xa95e62f]: lock   
libenergyplusapi.so.22.2.0[0xa95e630]: addq   $0x1, 0x6f5c838(%rip)
libenergyplusapi.so.22.2.0[0xa95e638]: jmp    0xa964218
libenergyplusapi.so.22.2.0[0xa95e63d]: endbr64 
libenergyplusapi.so.22.2.0[0xa95e6

libenergyplusapi.so.22.2.0[0xa95f958]: lock   
libenergyplusapi.so.22.2.0[0xa95f959]: addq   $0x1, 0x6f5531f(%rip)
libenergyplusapi.so.22.2.0[0xa95f961]: leaq   -0x300(%rbp), %rax
libenergyplusapi.so.22.2.0[0xa95f968]: movq   %rax, %rdi
libenergyplusapi.so.22.2.0[0xa95f96b]: callq  0xc658660
libenergyplusapi.so.22.2.0[0xa95f970]: lock   
libenergyplusapi.so.22.2.0[0xa95f971]: addq   $0x1, 0x6f5b93f(%rip)
libenergyplusapi.so.22.2.0[0xa95f979]: leaq   -0x290(%rbp), %rax
libenergyplusapi.so.22.2.0[0xa95f980]: movq   %rax, %rdi
libenergyplusapi.so.22.2.0[0xa95f983]: callq  0xc658f60
libenergyplusapi.so.22.2.0[0xa95f988]: lock   
libenergyplusapi.so.22.2.0[0xa95f989]: addq   $0x1, 0x6f5b92f(%rip)
libenergyplusapi.so.22.2.0[0xa95f991]: leaq   -0x240(%rbp), %rax
libenergyplusapi.so.22.2.0[0xa95f998]: movq   %rax, %rdi
libenergyplusapi.so.22.2.0[0xa95f99b]: callq  0xc658f60
libenergyplusapi.so.22.2.0[0xa95f9a0]: lock   
libenergyplusapi.so.22.2.0[0xa95f9a1]: addq   $0x1, 0x6f5b91f(%rip)
libene

libenergyplusapi.so.22.2.0[0xa960c3f]: movq   %rax, %rbx
libenergyplusapi.so.22.2.0[0xa960c42]: lock   
libenergyplusapi.so.22.2.0[0xa960c43]: addq   $0x1, 0x6f5555d(%rip)
libenergyplusapi.so.22.2.0[0xa960c4b]: leaq   -0x80(%rbp), %rax
libenergyplusapi.so.22.2.0[0xa960c4f]: movq   %rax, %rdi
libenergyplusapi.so.22.2.0[0xa960c52]: callq  0xc6586d0
libenergyplusapi.so.22.2.0[0xa960c57]: lock   
libenergyplusapi.so.22.2.0[0xa960c58]: addq   $0x1, 0x6f5aab8(%rip)
libenergyplusapi.so.22.2.0[0xa960c60]: jmp    0xa960c72
libenergyplusapi.so.22.2.0[0xa960c62]: endbr64 
libenergyplusapi.so.22.2.0[0xa960c66]: movq   %rax, %rbx
libenergyplusapi.so.22.2.0[0xa960c69]: lock   
libenergyplusapi.so.22.2.0[0xa960c6a]: addq   $0x1, 0x6f55526(%rip)
libenergyplusapi.so.22.2.0[0xa960c72]: leaq   -0x300(%rbp), %rax
libenergyplusapi.so.22.2.0[0xa960c79]: movq   %rax, %rdi
libenergyplusapi.so.22.2.0[0xa960c7c]: callq  0xc658660
libenergyplusapi.so.22.2.0[0xa960c81]: lock   
libenergyplusapi.so.22.2.0[0xa960c8

libenergyplusapi.so.22.2.0[0xa962023]: addq   $0x1, 0x6f59b2d(%rip)
libenergyplusapi.so.22.2.0[0xa96202b]: jmp    0xa96203d
libenergyplusapi.so.22.2.0[0xa96202d]: endbr64 
libenergyplusapi.so.22.2.0[0xa962031]: movq   %rax, %rbx
libenergyplusapi.so.22.2.0[0xa962034]: lock   
libenergyplusapi.so.22.2.0[0xa962035]: addq   $0x1, 0x6f556f3(%rip)
libenergyplusapi.so.22.2.0[0xa96203d]: leaq   -0x80(%rbp), %rax
libenergyplusapi.so.22.2.0[0xa962041]: movq   %rax, %rdi
libenergyplusapi.so.22.2.0[0xa962044]: callq  0xc6586d0
libenergyplusapi.so.22.2.0[0xa962049]: lock   
libenergyplusapi.so.22.2.0[0xa96204a]: addq   $0x1, 0x6f59b0e(%rip)
libenergyplusapi.so.22.2.0[0xa962052]: jmp    0xa962064
libenergyplusapi.so.22.2.0[0xa962054]: endbr64 
libenergyplusapi.so.22.2.0[0xa962058]: movq   %rax, %rbx
libenergyplusapi.so.22.2.0[0xa96205b]: lock   
libenergyplusapi.so.22.2.0[0xa96205c]: addq   $0x1, 0x6f556bc(%rip)
libenergyplusapi.so.22.2.0[0xa962064]: leaq   -0xa0(%rbp), %rax
libenergyplusapi.so.22.2

libenergyplusapi.so.22.2.0[0xa963543]: lock   
libenergyplusapi.so.22.2.0[0xa963544]: addq   $0x1, 0x6f563ac(%rip)
libenergyplusapi.so.22.2.0[0xa96354c]: leaq   -0x80(%rbp), %rax
libenergyplusapi.so.22.2.0[0xa963550]: movq   %rax, %rdi
libenergyplusapi.so.22.2.0[0xa963553]: callq  0xc6586d0
libenergyplusapi.so.22.2.0[0xa963558]: lock   
libenergyplusapi.so.22.2.0[0xa963559]: addq   $0x1, 0x6f58ad7(%rip)
libenergyplusapi.so.22.2.0[0xa963561]: jmp    0xa963573
libenergyplusapi.so.22.2.0[0xa963563]: endbr64 
libenergyplusapi.so.22.2.0[0xa963567]: movq   %rax, %rbx
libenergyplusapi.so.22.2.0[0xa96356a]: lock   
libenergyplusapi.so.22.2.0[0xa96356b]: addq   $0x1, 0x6f56375(%rip)
libenergyplusapi.so.22.2.0[0xa963573]: leaq   -0xa0(%rbp), %rax
libenergyplusapi.so.22.2.0[0xa96357a]: movq   %rax, %rdi
libenergyplusapi.so.22.2.0[0xa96357d]: callq  0xc6586d0
libenergyplusapi.so.22.2.0[0xa963582]: lock   
libenergyplusapi.so.22.2.0[0xa963583]: addq   $0x1, 0x6f58ab5(%rip)
libenergyplusapi.so.22.2.

In [81]:
process.Continue()

success

In [82]:
LLDBState(process.GetState())

<LLDBState.Stopped: 5>

In [83]:
LLDBState(process.GetState())

<LLDBState.Stopped: 5>

In [84]:
process.Continue()

success

In [85]:
if state == lldb.eStateExited:
    print("program has exited...")
else:
    print('Unexpected process state: %s, killing process...' % debugger.StateAsCString (state))
    process.Kill()

Unexpected process state: stopped, killing process...
